# TRABAJO DE PYTHON

### Este trabajo cuenta el 30% de la nota. 

### Resuelve los siguientes ejercicios en Python

#### Utiliza tantas celdas de código como necesites

#### 1.- Busca la secuencia del gen CNTNAP2 (cromosma 7) del genoma humano. Descarga la secuencia en formato FASTA e introdúcela en este Notebook . (1 pto)

In [1]:
secuenciaFASTA=open("gene.fna")
secuenciaGEN=secuenciaFASTA.read()
secuenciaFASTA.close()

#### 2.- Muestre el encabezado y la secuencia y guarde cada uno en variables separadas. Elimine el elemento "\n" del encabezado con replace() si es que lo tiene. ¿Cual es la longitud de la secuencia?. (1 pto)

In [2]:
secuenciaFASTA = open("gene.fna", "r")
encabezado = secuenciaFASTA.readline().replace("\n", "")
lineas = secuenciaFASTA.readlines()
secuenciaFASTA.close()

secuencia = "".join([linea.replace("\n", "") for linea in lineas])

print("Encabezado:", encabezado)
print("Secuencia (primeros 100 caracteres):", secuencia[:100])

longitud = len(secuencia)
print("Longitud de la secuencia:", longitud)

with open("secuencia_salida.txt", "w") as f:
    f.write(secuencia)

Encabezado: >NC_000007.14:146116801-148420998 CNTNAP2 [organism=Homo sapiens] [GeneID=26047] [chromosome=7]
Secuencia (primeros 100 caracteres): CTTCAAGAACCCTACGGAGAGTCGGACTGCATCTCCGCAGCGAGCTCTTGGAGCGCCGCCGGCCGGGAGGCGAAGGATGCAGGCGGCTCCGCGCGCCGGC
Longitud de la secuencia: 4812613


#### 3.- Para el encabezado, extrae empleando expresiones regulares el identificador. (1pto)

In [3]:
import re

with open("gene.fna", "r") as secuenciaFASTA:
    encabezado = secuenciaFASTA.readline().replace("\n", "")
    
match = re.match(r"^>(\S+)", encabezado)
if match:
    identificador = match.group(1)
else:
    identificador = None
    
print("Identificador:", identificador)

Identificador: NC_000007.14:146116801-148420998


#### 4.- ¿Cuál es el porcentaje de GC de la secuencia? (1 pto)

In [4]:
with open("gene.fna", "r") as secuenciaFASTA:
    encabezado = secuenciaFASTA.readline().replace("\n", "")  
    lineas = secuenciaFASTA.readlines()  

secuencia = "".join([linea.replace("\n", "") for linea in lineas])

gc_count = secuencia.count("G") + secuencia.count("C")

porcentaje_gc = (gc_count / len(secuencia)) * 100

print("Porcentaje de GC:", porcentaje_gc)

Porcentaje de GC: 37.73779441646357


#### 5.- Devuelve la secuencia de ARN que surgiría a partir de la siguiente secuencia. Recuerda que la secuencia de ARN resultante tiene que ser complementaria a la de ADN. (1 pto)

In [5]:
with open("gene.fna", "r") as archivo:
    encabezado = archivo.readline().strip()
    secuencia = "".join(linea.strip() for linea in archivo)

complemento = {
    "A": "U",
    "T": "A",
    "C": "G",
    "G": "C"
}

secuencia_ARN = "".join([complemento.get(base, base) for base in secuencia])

with open("secuencia_ARN.fna", "w") as f:
    f.write(secuencia_ARN)

print("Secuencia de ARN guardada en 'secuencia_ARN.fna'")

Secuencia de ARN guardada en 'secuencia_ARN.fna'


#### 6.- Realiza una función que realice una digestión con las siguientes enzimas de restricción en nuestra secuencia. La función tiene que devolver la siguiente información: (2 pto)
1. Enzimas que tienen sitios de corte en la secuencia y posición (o posiciones de corte)
2. Enzimas que no tienen sitios de corte (si las hay)
3. Resultado de la digestión: los fragmentos resultantes de nuestra secuencia
4. Indicar número y tamaño de cada fragmento

In [6]:
enzR = {
    'HindIII' : 'A*AGCTT',
    'BamHI' : 'G*GATCC',
    'AluI' : 'AG*CT',
    'Sau3AI' : '*GATC',
    'EcoRI' : 'G*AATTC'
}

In [7]:
def sitios_corte(secuencia, enzimas):
    resultados = {}
    secuencia = secuencia.upper()

    for nombre, patron in enzimas.items():
        sitio = patron.replace("*", "")
        corte = patron.index("*")
        posiciones = []
        for i in range(len(secuencia) - len(sitio)):
            if secuencia[i:i+len(sitio)] == sitio:
                posiciones.append(i + corte + 1)
        if posiciones:
            resultados[nombre] = posiciones
    return resultados
    
with open("gene.fna", "r") as f:
    f.readline()  
    secuencia = "".join(linea.strip() for linea in f)
    
cortes = sitios_corte(secuencia, enzR)

with open("cortes_enzimas.txt", "w") as out:
    out.write("Enzimas que tienen sitios de corte y posiciones:\n")
    for enzima, posiciones in cortes.items():
        out.write(f"{enzima}: {posiciones}\n")

print("Resultados guardados en 'cortes_enzimas.txt'")

Resultados guardados en 'cortes_enzimas.txt'


In [8]:
sin_corte = [enzima for enzima in enzR if enzima not in cortes]
with open("enzimas_sin_corte.txt", "w") as out:
    if sin_corte:
        out.write("Enzimas que NO tienen sitios de corte:\n")
        for enzima in sin_corte:
            out.write(f"  {enzima}\n")
    else:
        out.write("Todas las enzimas tienen al menos un sitio de corte.\n")

print("Resultados guardados en 'enzimas_sin_corte.txt'")

Resultados guardados en 'enzimas_sin_corte.txt'


In [9]:
def digestión_fragmentos(secuencia, enzimas):
    secuencia = secuencia.upper()
    cortes_totales = []

    for nombre, patron in enzimas.items():
        sitio = patron.replace("*", "")
        corte = patron.index("*")
        pos = secuencia.find(sitio)
        while pos != -1:
            cortes_totales.append(pos + corte)
            pos = secuencia.find(sitio, pos + 1)

    cortes_totales = sorted(cortes_totales)

    inicio = 0
    fragmentos_resultantes = []
    for corte in cortes_totales:
        fragmentos_resultantes.append(secuencia[inicio:corte])
        inicio = corte
    fragmentos_resultantes.append(secuencia[inicio:])

    return fragmentos_resultantes

with open("gene.fna", "r") as f:
    f.readline() 
    secuencia = "".join(linea.strip() for linea in f)

fragmentos = digestión_fragmentos(secuencia, enzR)

with open("fragmentos_digestión.txt", "w") as out:
    for i, frag in enumerate(fragmentos, 1):
        out.write(f">Fragmento_{i}\n")
        out.write(f"{frag}\n")
print("Todos los fragmentos guardados en 'fragmentos_digestión.txt'")

Todos los fragmentos guardados en 'fragmentos_digestión.txt'


In [11]:
fragmentos = []
with open("fragmentos_digestión.txt", "r", encoding="utf-8") as f:
    for linea in f:
        frag = linea.strip()
        if frag:
            fragmentos.append(frag)

num_fragmentos = len(fragmentos)
tamaños = [len(frag) for frag in fragmentos]

with open("fragmentos_info.txt", "w", encoding="utf-8") as out:
    out.write(f"Número total de fragmentos: {num_fragmentos}\n\n")
    out.write("Tamaño de cada fragmento:\n")
    for i, tam in enumerate(tamaños, 1):
        out.write(f"Fragmento {i}: {tam} bases\n")

print("Archivo 'fragmentos_info.txt'")


Archivo 'fragmentos_info.txt'


#### 7.- Realiza una función que mediante la introducción de una secuencia de ADN devuelva lo siguiente: (3pto)
1. Todos los ORFs posibles que puedan surgir de la secuencia.
2. Selecciona los 6 ORFs más largos e indica si corresponden a la strand positiva o negativa.
3. Devuelve como mejor predicción, el más largo de todos.
4. Calcula el porcentaje de aminoácidos aromáticos de esa proteína elegida y su longitud relativa a la secuencia original de ADN.

In [6]:
secuenciaFASTA = open("gene.fna")
secuenciaGEN = secuenciaFASTA.read().replace("\n", "").upper()
secuenciaFASTA.close()

inicio = "ATG"
paradas = ["TAA", "TAG", "TGA"]

def encontrar_orfs(seq):
    orfs = []
    for i in range(len(seq) - 2):
        if seq[i:i+3] == inicio:
            for j in range(i+3, len(seq) - 2, 3):
                if seq[j:j+3] in paradas:
                    orfs.append((len(orfs) + 1, seq[i:j+3], "positiva"))
                    break
    
    complementario = seq.translate(str.maketrans("ATGC", "TACG"))[::-1]
    for i in range(len(complementario) - 2):
        if complementario[i:i+3] == inicio:
            for j in range(i+3, len(complementario) - 2, 3):
                if complementario[j:j+3] in paradas:
                    orfs.append((len(orfs) + 1, complementario[i:j+3], "negativa"))
                    break
    return orfs

orfs_encontrados = encontrar_orfs(secuenciaGEN)

print(f"Total ORFs encontrados: {len(orfs_encontrados)}")
for numero, orf, strand in orfs_encontrados:
    print(f"ORF {numero}: longitud {len(orf)}, strand {strand}")

with open("orfs_encontrados.txt", "w", encoding="utf-8") as archivo:
    archivo.write(f"Total ORFs encontrados: {len(orfs_encontrados)}\n\n")
    for numero, orf, strand in orfs_encontrados:
        archivo.write(f"ORF {numero}: longitud {len(orf)}, strand {strand}\n")
        archivo.write(f"Secuencia: {orf}\n\n")

for numero, orf, strand in orfs_encontrados:
    print(f"ORF {numero}: longitud {len(orf)}, strand {strand}")

Total ORFs encontrados: 189613
ORF 1: longitud 105, strand positiva
ORF 2: longitud 54, strand positiva
ORF 3: longitud 135, strand positiva
ORF 4: longitud 33, strand positiva
ORF 5: longitud 6, strand positiva
ORF 6: longitud 15, strand positiva
ORF 7: longitud 120, strand positiva
ORF 8: longitud 45, strand positiva
ORF 9: longitud 15, strand positiva
ORF 10: longitud 60, strand positiva
ORF 11: longitud 9, strand positiva
ORF 12: longitud 12, strand positiva
ORF 13: longitud 45, strand positiva
ORF 14: longitud 99, strand positiva
ORF 15: longitud 93, strand positiva
ORF 16: longitud 48, strand positiva
ORF 17: longitud 6, strand positiva
ORF 18: longitud 21, strand positiva
ORF 19: longitud 123, strand positiva
ORF 20: longitud 36, strand positiva
ORF 21: longitud 6, strand positiva
ORF 22: longitud 42, strand positiva
ORF 23: longitud 87, strand positiva
ORF 24: longitud 45, strand positiva
ORF 25: longitud 24, strand positiva
ORF 26: longitud 9, strand positiva
ORF 27: longitud 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



ORF 142401: longitud 6, strand negativa
ORF 142402: longitud 24, strand negativa
ORF 142403: longitud 18, strand negativa
ORF 142404: longitud 63, strand negativa
ORF 142405: longitud 123, strand negativa
ORF 142406: longitud 72, strand negativa
ORF 142407: longitud 78, strand negativa
ORF 142408: longitud 72, strand negativa
ORF 142409: longitud 24, strand negativa
ORF 142410: longitud 51, strand negativa
ORF 142411: longitud 18, strand negativa
ORF 142412: longitud 6, strand negativa
ORF 142413: longitud 174, strand negativa
ORF 142414: longitud 15, strand negativa
ORF 142415: longitud 30, strand negativa
ORF 142416: longitud 75, strand negativa
ORF 142417: longitud 72, strand negativa
ORF 142418: longitud 69, strand negativa
ORF 142419: longitud 15, strand negativa
ORF 142420: longitud 48, strand negativa
ORF 142421: longitud 81, strand negativa
ORF 142422: longitud 45, strand negativa
ORF 142423: longitud 42, strand negativa
ORF 142424: longitud 12, strand negativa
ORF 142425: long

In [6]:
top6_orfs = sorted(orfs_encontrados, key=lambda x: len(x[1]), reverse=True)[:6]
print("\nTop 6 ORFs más largos:\n")
for numero, secuencia, strand in top6_orfs:
    print(f"ORF {numero}: longitud {len(secuencia)}, strand {strand}")


Top 6 ORFs más largos:

ORF 16041: longitud 2115, strand positiva
ORF 65389: longitud 2115, strand positiva
ORF 16044: longitud 1794, strand positiva
ORF 65392: longitud 1794, strand positiva
ORF 154770: longitud 1719, strand negativa
ORF 16047: longitud 1692, strand positiva


In [ ]:
Aclaracion: Para la parte 3 y 4 vamos a a trabajar con el ORF16041 aunque el ORF65389 tambien seria bueno ya que tiene la misma longitud 

In [8]:
mejor_orf = [orf for orf in orfs_encontrados if orf[0] == 16041][0]

numero, secuencia_orf, strand = mejor_orf

print(f"Mejor predicción:")
print(f"  ORF {numero}")
print(f"  Longitud: {len(secuencia_orf)}")
print(f"  Strand: {strand}")
print(f"  Secuencia (primeros 60 nt): {secuencia_orf[:60]}...")

with open("mejor_orf.txt", "w", encoding="utf-8") as archivo:
    archivo.write("=== Mejor ORF encontrado ===\n")
    archivo.write(f"ORF {numero}\n")
    archivo.write(f"Longitud: {len(secuencia_orf)}\n")
    archivo.write(f"Strand: {strand}\n")
    archivo.write(f"Secuencia:\n{secuencia_orf}\n")

print("\nArchivo 'mejor_orf.txt'")

Mejor predicción:
  ORF 16041
  Longitud: 2115
  Strand: positiva
  Secuencia (primeros 60 nt): ATGGACACATTCCTCGACACATACACTCTCCCAAGACTAAACCAGGAAGAAGTTGAATCT...

Archivo 'mejor_orf.txt'


In [9]:
codigo_genetico = {
    'TTT':'F','TTC':'F','TTA':'L','TTG':'L',
    'CTT':'L','CTC':'L','CTA':'L','CTG':'L',
    'ATT':'I','ATC':'I','ATA':'I','ATG':'M',
    'GTT':'V','GTC':'V','GTA':'V','GTG':'V',
    'TCT':'S','TCC':'S','TCA':'S','TCG':'S',
    'CCT':'P','CCC':'P','CCA':'P','CCG':'P',
    'ACT':'T','ACC':'T','ACA':'T','ACG':'T',
    'GCT':'A','GCC':'A','GCA':'A','GCG':'A',
    'TAT':'Y','TAC':'Y','TAA':'*','TAG':'*',
    'CAT':'H','CAC':'H','CAA':'Q','CAG':'Q',
    'AAT':'N','AAC':'N','AAA':'K','AAG':'K',
    'GAT':'D','GAC':'D','GAA':'E','GAG':'E',
    'TGT':'C','TGC':'C','TGA':'*','TGG':'W',
    'CGT':'R','CGC':'R','CGA':'R','CGG':'R',
    'AGT':'S','AGC':'S','AGA':'R','AGG':'R',
    'GGT':'G','GGC':'G','GGA':'G','GGG':'G'
}

proteina = ""
for i in range(0, len(secuencia_orf)-2, 3):
    codon = secuencia_orf[i:i+3]
    aa = codigo_genetico.get(codon, "X")  
    if aa == "*":  
        break
    proteina += aa

aromaticos = ['F', 'Y', 'W']
num_aromaticos = sum(1 for aa in proteina if aa in aromaticos)
porcentaje_aromaticos = (num_aromaticos / len(proteina)) * 100

longitud_relativa = (len(proteina) / len(secuencia_orf)) * 100

print(f"Longitud de la proteína: {len(proteina)} aminoácidos")
print(f"Porcentaje de aminoácidos aromáticos: {porcentaje_aromaticos:.2f}%")
print(f"Longitud relativa respecto a la secuencia de ADN: {longitud_relativa:.2f}%")

Longitud de la proteína: 704 aminoácidos
Porcentaje de aminoácidos aromáticos: 10.23%
Longitud relativa respecto a la secuencia de ADN: 33.29%
